In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
import os
import json
import itertools
import random
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import regex as re
import numpy as np
import math



# Fehleranalyse

In [3]:
# Neue Code

import os
import pandas as pd
from glob import glob
import plotly.graph_objects as go


def erroranalyse_relation_new(folder_path, relation_title=None):
    # ------------------------------------------------------------
    # 1. Alle CSVs zusammenführen
    # ------------------------------------------------------------
    csv_files = sorted(glob(os.path.join(folder_path, "*.csv")))
    if not csv_files:
        raise FileNotFoundError(f"Keine CSV-Dateien in {folder_path} gefunden!")

    merged_data = {}
    for file in csv_files:
        shot_label = os.path.basename(file).split(".")[0]
        df = pd.read_csv(file)  # evtl. encoding="utf-8" ergänzen

        # Gold-Spalte einmalig übernehmen
        if "answer_token" not in merged_data:
            merged_data["answer_token"] = df["answer_token"]

        # Für eine 1-Shot-Datei zusätzlich das letzte Prompt-Template speichern
        if "last_template" not in merged_data and "1shot" in shot_label:
            merged_data["last_template"] = (
                df["prompt"].apply(lambda x: x.strip().split("\n")[-1])
            )

        # Predictions pro Shot-Konfiguration
        merged_data[shot_label.split("_")[-1]] = df["predicted_top1_token"]

    merged_df = pd.DataFrame(merged_data)

    # ------------------------------------------------------------
    # 2. Spalten sinnvoll sortieren
    # ------------------------------------------------------------
    ordered_cols = ["answer_token"]
    if "last_template" in merged_df.columns:          # <-- nur falls vorhanden
        ordered_cols.append("last_template")

    shot_cols = sorted(
        [c for c in merged_df.columns if c.endswith("shot")],
        key=lambda x: int(x.replace("shot", ""))
    )
    ordered_cols.extend(shot_cols)
    merged_df = merged_df[ordered_cols]               # garantiert jetzt vorhanden

    # ------------------------------------------------------------
    # 3. Hilfsfunktionen
    # ------------------------------------------------------------
    def tokenize(s):
        return str(s).split()

    gold_col  = "answer_token"
    pred_cols = shot_cols

    # Zeilen markieren, in denen mindestens ein Shot falsch ist
    row_wrong = merged_df.apply(
        lambda r: any(tokenize(r[c]) != tokenize(r[gold_col]) for c in pred_cols),
        axis=1
    )

    total_samples = len(merged_df)

    # Die Spalte mit dem Prompt/Template bestimmen
    group_col_candidates = ["prompt", "last_template", "template"]
    group_col = next((c for c in group_col_candidates if c in merged_df.columns), None)
    if group_col is None:
        raise KeyError("Keine geeignete Template-/Prompt-Spalte gefunden!")

    prompts_with_error = merged_df.loc[row_wrong, group_col].unique()
    wrong_df = merged_df[merged_df[group_col].isin(prompts_with_error)]

    # Fehler pro Shot zählen
    error_counts = {
        col: sum(tokenize(r[col]) != tokenize(r[gold_col]) for _, r in wrong_df.iterrows())
        for col in pred_cols
    }

    # ------------------------------------------------------------
    # 4. Plotly-Tabelle zusammenstellen
    # ------------------------------------------------------------
    values, colors = [], []

    # erste Spalte = DataFrame-Index
    values.append([""] + list(wrong_df.index))
    colors.append(["white"] * (len(wrong_df) + 1))

    def col_vals(col):
        body = [
            " ".join(tokenize(v)) if col in pred_cols else v
            for v in wrong_df[col]
        ]
        if col == gold_col:
            header = f"Token/Subtoken: {total_samples}"
            return [header] + body
        if col in pred_cols:
            return [f"Error: {error_counts[col]}"] + body
        return [""] + body

    def col_cols(col):
        if col in pred_cols:
            body = [
                "#d4edda" if tokenize(v) == tokenize(g) else "#f8d7da"
                for v, g in zip(wrong_df[col], wrong_df[gold_col])
            ]
        else:
            body = ["white"] * len(wrong_df)
        return ["white"] + body

    for c in wrong_df.columns:
        values.append(col_vals(c))
        colors.append(col_cols(c))

    # Tabelle rendern
    title = relation_title or os.path.basename(folder_path)
    fig = go.Figure(data=[go.Table(
        header=dict(
            values=["Index"] + list(wrong_df.columns),
            fill_color="#333333",
            font=dict(color="white", size=12)
        ),
        cells=dict(
            values=values,
            fill_color=colors,
            font=dict(color="black", size=11),
            height=25
        )
    )])

    fig.update_layout(
        height=min(600, 40 + 25 * (len(wrong_df) + 1)),
        title=f"Erroranalyse: {title}",
        margin=dict(l=0, r=0, t=40, b=0)
    )
    fig.show()


In [4]:
# ---------- Abhängigkeiten (falls noch nicht installiert) ----------
!pip install -q -U plotly==6.1.1 kaleido==0.2.1 pandas

import os, re, pandas as pd, plotly.graph_objects as go
from glob import glob

def export_compact_table(folder_path, rows_to_show, out_name,
                         out_dir="/content/drive/MyDrive/master_thesis/ploted_data_it",
                         only_errors=False,
                         show_title=False):              # <- NEUER PARAMETER
    """
    Erstellt aus mehreren .csv-Dateien eine farbcodierte Plotly-Tabelle,
    speichert sie als PDF/PNG und zeigt sie im Notebook an.

    Parameters
    ----------
    folder_path : str
        Ordner mit den .csv-Ergebnissen (eine Datei pro Shot-Einstellung).
    rows_to_show : list[int]
        Zeilen-Indizes, die in der Tabelle erscheinen sollen.
    out_name : str
        Basisname für die Ausgabedateien.
    out_dir : str, optional
        Zielordner für PDF/PNG.
    only_errors : bool, optional
        Wenn True, werden nur Zeilen mit mindestens einem Fehl-Token gezeigt.
    show_title : bool, optional
        Bestimmt, ob im Plot eine Titelüberschrift angezeigt wird.
    """

    # 1) CSVs mergen -------------------------------------------------------
    merged = {}
    for f in sorted(glob(os.path.join(folder_path, "*.csv"))):
        shot = os.path.basename(f).split(".")[0]
        df   = pd.read_csv(f, encoding="utf-8-sig")
        merged.setdefault("answer_token", df["answer_token"])
        if "last_template" not in merged and "1shot" in shot:
            merged["last_template"] = df["prompt"].str.strip().str.split("\n").str[-1]
        merged[shot.split("_")[-1]] = df["predicted_top1_token"]
    df = pd.DataFrame(merged)

    # 2) Fehlerfilter ------------------------------------------------------
    tok = lambda s: str(s).split()

    # --- NUMERISCH sortierte Shot-Spalten -------------------------------
    import re as _re
    shot_cols = sorted(
        [c for c in df if c.endswith("shot")],
        key=lambda s: int(_re.search(r"\d+", s).group())
    )

    wrong = df.apply(lambda r: any(tok(r[c]) != tok(r["answer_token"]) for c in shot_cols),
                     axis=1)
    base  = df[wrong] if only_errors else df

    # 3) Gewünschte Zeilen -------------------------------------------------
    sub = base.loc[[i for i in rows_to_show if i in base.index]]
    sub = sub.rename(columns={"answer_token": "Gold Token",
                              "last_template": "Template"})

    # --- Shot-Überschriften hübscher: 0-Shot, 1-Shot, … -----------------
    rename_map = {c: c.replace("shot", "-Shot") for c in shot_cols}
    sub = sub.rename(columns=rename_map)

    ordered_cols = ["Gold Token", "Template"] + list(rename_map.values())
    sub = sub[ordered_cols]

    # 4) Farben vorbereiten -----------------------------------------------
    colors = []
    for c in sub.columns:
        if c.endswith("-Shot"):
            colors.append(["#d4edda" if tok(v) == tok(g) else "#f8d7da"
                           for v, g in zip(sub[c], sub["Gold Token"])])
        else:
            colors.append(["white"] * len(sub))

    # 5) Plotly-Table ------------------------------------------------------
    col_values = [sub[c].apply(lambda x: " ".join(tok(x)) if c.endswith("-Shot") else x).tolist()
                  for c in sub.columns]

    fig = go.Figure(go.Table(
        header=dict(values=list(sub.columns), fill_color="#333",
                    font=dict(color="white", size=12)),
        cells=dict(values=col_values, fill_color=colors,
                   font=dict(color="black", size=11), height=26)))

    # ---------- kompakte Breite & Layout ----------
    w = 150 * 2 + 90 * len(rename_map)        # Breite in px
    h = 50 * (len(sub) + 1) + 40              # Höhe  in px

    if show_title:                            # Titel optional
        fig.update_layout(width=w, height=h, title=out_name,
                          margin=dict(l=0, r=0, t=40, b=0))
    else:
        fig.update_layout(width=w, height=h,
                          margin=dict(l=0, r=0, t=20, b=0))

    # 6) speichern ---------------------------------------------------------
    os.makedirs(out_dir, exist_ok=True)
    safe = re.sub(r"[^0-9A-Za-z_\-]+", "_", out_name).strip("_")
    pdf  = os.path.join(out_dir, f"{safe}.pdf")
    png  = os.path.join(out_dir, f"{safe}.png")
    fig.write_image(pdf, width=w, height=h, scale=1)
    fig.write_image(png, width=w, height=h, scale=1)
    print("✔︎ PDF :", pdf)
    print("✔︎ PNG :", png)
    fig.show()



     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 91.2/91.2 kB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.1/16.1 MB 96.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.9/79.9 MB 27.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.4/12.4 MB 119.6 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires pandas==2.2.2, but you have pandas 2.3.1 which is incompatible.
dask-cudf-cu12 25.6.0 requires pandas<2.2.4dev0,>=2.0, but you have pandas 2.3.1 which is incompatible.
cudf-cu12 25.6.0 requires pandas<2.2.4dev0,>=2.0, but you have pandas 2.3.1 which is incompatible.


#factual



###personen bezogene facten


#### person mother

In [ ]:
#203-2012
"""
Michelangelo (Indices 203–212):
Das korrekte Goldlabel ist „Francesca di Neri del Miniato di Siena“.
Das Modell generiert mehrfach italienisch typische Namen und Fragmente wie „Maria“, „Grazia“, „Lucrezia“, und auch Wörter wie „Medici“,
die eindeutig italienisch sind und klar auf einen italienischen sprachlichen Bias hinweisen"""

#Arnold Schwarzenegger (Index 848):
#Statt des korrekten Gold-Labels „Aurelia“ generiert das Modell konstant den Namen „Maria“, ein typisch italienischer weiblicher Vorname.

#Zudem taucht mehrfach das Wort „madre“

#33
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/person_mother")

####personfather

In [ ]:
"""
normalize("person_father"): [
        ("Hailey Bieber", "Stephen Baldwin"),
        ("Don Johnson", "Fredie Wayne Johnson"),
        ("Bronny James", "LeBron James"),
        ("Michael Wayans", "Damon Wayans"),
        ("Trinity Rodman", "Dennis Rodman"),
        ("Allison Williams","Brian Williams"),
        ("Deacon Phillippe", "Ryan Phillippe"),
        ("Sofia Richie","Lionel Richie"),
        ("Jesse Bongiovi", "Jon Bon Jovi"),
        ("John Owen Lowe","Rob Lowe")

        #subtokens 253-260
       # "subject": "Paul Cezanne",
       #     "object": "Louis-Auguste Cezanne"

       #      Modell-Antwort: Louis Auguste Cezanne (ohne Bindenstrich)..
       # 366-367
#Joseph Léopold Sigisbert Hugo 188-196
        # tokenisierungfehler zero shot 206-210
"""

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/person_father")

#### person occupation

In [ ]:
"""

# zero shot: fängt mir ein an: ein schauspieler..(kennt die antwort)
# , die erste Frau?... semantisch nicht gleich
Eine Person mehere Berufe. Verschiedene Shots generieren verschiedene Antworten

# gleiche phänomen wie englisch: 10-13 schauspieler gold label...2 shot auch so.. 1, 3-10=schauspielerin "Pat Crowley" es ist eine Frau
"""

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/person_occupation")

#### person university

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/person_university")

####person plays instrument

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/person_plays_instrument")

#### person band lead singer

In [ ]:
 normalize("person_band_lead_singer"): [
    ("Hayley Williams", "Paramore"),
    ("Brandon Flowers", "The Killers"),
    ("Debbie Harry", "Blondie"),
    ("Thom Yorke", "Radiohead"),
    ("Amy Lee", "Evanescence"),
    ("Matt Bellamy", "Muse"),
    ("James Murphy", "LCD Soundsystem"),
    ("Win Butler", "Arcade Fire"),
    ("Shirley Manson", "Garbage"),
    ("Brittany Howard", "Alabama Shakes")
],

"""
falsch, weil objekt einen leerzeichen am ende hat.
"subject": "Jon Bon Jovi",
            "object": "Bon Jovi " # 44   eigentlich keine fehler ab 3 shots

#1. Subtokenisierung (Token-Splitting)
Viele Bandnamen bestehen aus mehreren Tokens (z.B. „AC/DC“, „Red Hot Chili Peppers“). Wenn das Modell nicht klar erkennt, wie der Bandname beginnt oder endet, generiert es „the“, „and“ oder „band“ als Platzhalter.
Beispiele:
Index 0–2 (AC/DC): Generierung von „the“, „band“, „,“ im Zero-Shot-Fall.
Index 5–6 (Coldplay): Generierung von „the“, „band“ im Zero-Shot-Fall.
Index 7–8 (Foo Fighters): Generierung von „the“ im Zero-Shot-Fall.
Index 16–17 (Metallica): Generierung von „the“, „band“ im Zero-Shot-Fall.

2. Frequenz-basierte Fehler (Frequency Bias)
Das Modell neigt dazu, besonders häufige Tokens aus dem Training zu wählen, wenn es unsicher ist. Tokens wie „the“ und „band“ sind sehr häufig und daher sichere Optionen aus Sicht des Modells.
Beispiele dafür:
Index 12 (Guns N' Roses): Modell generiert „and“ statt „N'“.
Index 20 (Queen): Modell generiert „the“ statt „Queen“.
Index 26 (The Rolling Stones): Generierung von „the“ alleine, aber korrekte Vervollständigung bei mehr Shots.




In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/person_band_lead_singer")

####person_plays_position_in_sport

In [ ]:
# #5-6 goaltender (Wird hauptsächlich im Eishockey verwendet.) ab 2 shots wird stattdessen goalkeeper verwendet (Wird primär im Fußball verwendet.
# Auch in Sportarten wie Handball, Feldhockey und Wasserball üblich.),
# im few shot beispiele ist genauso goalkkeepr
"""
Generische bzw. falsche Positionen:
„forward“, „defensive“, „defenseman“ statt spezifischer Positionen (z. B. „linebacker“, „midfielder“).
Beispiele:
Index 0: linebacker → „forward“
Index 7: linebacker → „defenseman“
Index 11: midfielder → „forward“
Index 45: midfielder → „Goal“


Typische Few-Shot-Fehlerarten:
Frequency Bias (dominierende Positionen aus den Shots):
Aufgrund mehrfach verwendeter Beispiele aus dem Fußball („midfielder“, „goalkeeper“, „forward“) wird bei Unsicherheit
häufig „goalkeeper“ generiert, selbst wenn andere Positionen erwartet werden.

Beispiele:
Index 1, 3, 8, 11, 21, 24, 39, 43, 45: midfielder → fälschlich als „goalkeeper“ vorhergesagt.



In [ ]:
"""("Patrick Mahomes", "Quarterback"),
         ("Manuel Neuer", "Torwart"),
        ("Toni Kroos", "Mittelfeldspieler"),
         ("Yadier Molina", "Fänger"),
        ("Ray Lewis", "Verteidiger"),
         ("Justin Verlander", "Werfer"),
        ("Marc-André Fleury", "Eishockeytorwart"),
         ("Luka Modrić", "Mittelfeldspieler"),
          ("Lionel Messi", "Stürmer"),
        ("Aaron Judge ","Außenfeldspieler"),
        ("Ronald Acuña Jr.", "Außenfeldspieler")"""


erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/person_plays_position_in_sport")

####person plays pro sport

In [ ]:
"""

"person plays pro sport": [
    ["Kylian Mbappé","Fußball"],
    ["Shohei Otani", "Baseball"],
    ["Jayson Tatum","Basketball"],
    ["Luciana Aymar","Hockeysport"],
    ["Josh Allen","Fußball"],
    ["Jamie Dwyer","Hockeysport"],
    ["Aaron Judge","Baseball"],
    [ "Novak Đoković","Tennis"],
    [
      "Joel Embiid",
      "Basketball"
    ],
    [
      "Lautaro Martínez",
      "Fußball"
    ]

zero shot: seit...1989  meiste fällen oder falshce token, die keine semantische bedeutung haben
few shot: # 2-6: übersetzung: Hockeysport : modeel generierung Eishocky
#17, 18 baseball, basketball kennt gut
# hockeysport wird immer als Eishockey
"""

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/person_plays_pro_sport")

#### superhero person

In [ ]:
("superhero_person"): [
    ("Moon Knight", "Marc Spector"),
    ("Doctor Fate", "Kent Nelson"),
    ("Nova", "Richard Rider"),
    ("Captain Atom", "Nathaniel Adam"),
    ("Plastic Man", "Patrick O'Brian"),
    ("Sentry", "Robert Reynolds"),
    ("Blue Marvel", "Adam Brashear"),
    ("Rorschach", "Walter Joseph Kovacs"),
    ("The Phantom", "Kit  Walker"),
    ("Kick-Ass", "Dave Lizewski")
    ],
"""
Unvollständige oder fehlerhafte Antwort aufgrund von Subtokenisierung
# 0 Kal
Unsinnige oder semantisch falsche Tokens
Beispiele:
Index 56-57 (Phoenix → Jean Grey; Ausgabe „not known“)

Zero-Shot hat viele Fehler durch unvollständige Subtokenisierung und komplett falsche Vorhersagen.
Few-Shot verbessert Performance, aber bei steigender Shot-Zahl entstehen Verwechslungen, falsche Subtokenisierung und unvollständige Antworten.
Optimale Ergebnisse um 3–4 Shots; mit zunehmender Anzahl an Shots treten erneut Fehler auf.

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/superhero_person")

### Orts-länderbezogene facten

####landmark on continent

In [ ]:
"landmark_on_continent"): [
        ("Eiffel Tower", "Europe"),
         ("Statue of Liberty", "North America"),
          ("Big Ben", "Europe"),
        ("Table Mountain", "Africa"),
         ("Mount Fuji", "Asia"),
          ("Machu Picchu", "South America"),
        ("Sydney Opera House", "Australia"),
         ("Colosseum", "Europe"),
          ("Mount Erebus", "Antarctica"),
        ("Uluru", "Australia")

        # von insgesamt 947 Tokens 916 das Label „Antarctica“ tragen.

        #700-704-705 ---> meist falsch vorkommende nord america statt an antarctida

In [5]:
#256-259
rows = [66,67,68, 116]

export_compact_table("/content/drive/MyDrive/master_thesis/dataset_multilingual/"
    "factual/it/result_10_accuracy/logits/permutation_0/landmark_on_continent",
    rows_to_show = rows,
    out_name     = "landmark_on_continent_it",
    only_errors  = False,
    show_title   = False          # <-- kein Titel im Plot
)

✔︎ PDF : /content/drive/MyDrive/master_thesis/ploted_data_it/landmark_on_continent_it.pdf
✔︎ PNG : /content/drive/MyDrive/master_thesis/ploted_data_it/landmark_on_continent_it.png


In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/landmark_on_continent")

####landmark in country

In [ ]:
"""("Eiffel Tower", "France"), ("Statue of Liberty", "United States"),
        ("Christ the Redeemer", "Brazil"), ("Big Ben", "United Kingdom"),
        ("Great Wall of China", "China"), ("Sydney Opera House", "Australia"),
        ("Taj Mahal", "India"), ("Mount Fuji", "Japan"),
        ("Burj Khalifa", "United Arab Emirates"), ("Colosseum", "Italy")"""
# probleme mit 0 shot kreis...



In [10]:
#256-259
rows = [30,31,89,103,104,211,212,213]

export_compact_table("/content/drive/MyDrive/master_thesis/dataset_multilingual/"
    "factual/it/result_10_accuracy/logits/permutation_0/landmark_in_country",
    rows_to_show = rows,
    out_name     = "landmark_in_country_it",
    only_errors  = False,
    show_title   = False          # <-- kein Titel im Plot
)

✔︎ PDF : /content/drive/MyDrive/master_thesis/ploted_data_it/landmark_in_country_it.pdf
✔︎ PNG : /content/drive/MyDrive/master_thesis/ploted_data_it/landmark_in_country_it.png


In [ ]:


erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/landmark_in_country")

####food from country

In [ ]:
 "food from country": [
    [
      "Souvlaki",
      "Griechenland"
    ],
    [
      "Ratatouille",
      "Frankreich"
    ],
    [
      "Kebab",
      "Türkei"
    ],
    [
      "Chatschapuri",
      "Georgia"
    ],
    [
      "Brigadeiro",
      "Brasilien"
    ],
    [
      "Gazpacho",
      "Spanien"
    ],
    [
      "Moules-frites",
      "Belgien"
    ],
    [
      "Poffertjes",
      "Niederlande"
    ],
    [
      "Tajine",
      "Marokko"
    ],
    [
      "Picarones",
      "Peru"
    ]
  ],

In [ ]:


erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/food_from_country")

####city in country

In [ ]:
  normalize("city_in_country"): [
        ("Paris", "France"),
        ("Tokyo", "Japan"),
        ("Berlin", "Germany"),
        ("Toronto", "Canada"),
        ("Madrid", "Spain"),
        ("Lisbon", "Portugal"),
        ("Cairo", "Egypt"),
        ("Rome", "Italy"),
        ("Seoul", "South Korea"),
        ("Athens", "Greece")
    ],

Im Zero-Shot-Szenario generiert das Modell zunächst häufig inkohärente oder fehlerhafte Token („di“, „uno“, „dei“), die keine korrekte Länderbezeichnung darstellen.

Bereits mit wenigen Shots (ab 1-Shot) verbessert sich die Modellleistung erheblich und erreicht ein stabileres Niveau.

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/city_in_country")

####country capital city

In [ ]:
 normalize("country_capital_city"): [
    ("Norway", "Oslo"), ("Finland", "Helsinki"), ("Denmark", "Copenhagen"),
    ("Netherlands", "Amsterdam"), ("Switzerland", "Bern"),
    ("Austria", "Vienna"), ("Belgium", "Brussels"), ("Czech Republic", "Prague"),
    ("Ireland", "Dublin"), ("Portugal", "Lisbon")
    ],

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/country_capital_city")


####country language

In [ ]:
"""
Zero shot problem mit model fängt mit il an. alle falsch dann generiert zählt aber alles falsch
mit 1 shot weniger fehler aber trotzdem fehlerrate hoch
ab2 shotstabil


Italienische Sprache
Im Zero-Shot-Ansatz treten umfassende Fehler auf, da das Modell typischerweise mit dem unpassenden Artikel „il“ beginnt, wodurch sämtliche Antworten als falsch gewertet werden. Bereits im 1-Shot-Ansatz verringert sich zwar die Fehlerrate, sie bleibt aber zunächst vergleichsweise hoch. Ab dem 2-Shot-Ansatz stabilisiert sich die Modellleistung deutlich. Das spezifische Problem bei der Sprache Chinas („Cinese“ statt „Mandarino“) bleibt jedoch weiterhin bestehen. Insgesamt zeigt sich ab dem 2-Shot-Szenario eine gute und stabile Performance.
"""

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/country_language")

####country largest city

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/country_largest_city")

####country currency

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/country_currency")

###Unternehmens- & Produktbezogene Fakten

#### product by company

In [ ]:
("product_by_company"): [
        ("Kindle", "Amazon"), ("Echo Dot", "Amazon"),
         ("Galaxy S22", "Samsung"),("PlayStation 5", "Sony"),
        ("ChatGPT", "OpenAI"),  ('iPhone 15', 'Apple'),
         ("Mi Band 6", "Xiaomi Inc."), ("ThinkPad X1 Carbon", "Lenovo"),
          ("Surface Pro 9", "Microsoft"), ("Nest Thermostat", "Google")
    ], #product by company 522
    #zero shot: the, a
    #few: 7 shot wiederholt von subjekt 250, 287,291,223,260,417
    # adobe und microsoft  273
    #,314
    # früher google jetzt MIT
    #meinst commen token Bais in Training, meisten Fäller große Unternehmen wie Microsoft , Google Amazon


In [ ]:
erroranalyse_relation_new ("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/product_by_company")

#### company ceo

In [ ]:
    normalize("company CEO"): [
    ("YouTube", "Neal Mohan"),
    ("Stripe", "Patrick Collison"),
    ("Spotify", "Daniel Ek"),
    ("Airbnb", "Brian Chesky"),
    ("OpenAI", "Sam Altman"),
    ("BioNTech", "Uğur Şahin"),
    ("Klarna", "Sebastian Siemiatkowski"),
    ("TikTok", "Shou Zi Chew"),
     ("IKEA", "Jesper Brodin"),
    ("Revolut", "Nikolay Storonsky")
],



#61-64 Ted Sarendos. Modell gint über alle shots (Reed Hastings) cofounder von netflix
#{ #76-78 Meg Whitemen ceo von Hewlett-Packard 1999-2005 (0-4)  ### aktuell CEO Antonio Neri
#5-10 For decades, Hewlett Packard Enterprise Company (HPE) and HP Inc. were part of the same company, the iconic Hewlett-Packard .Now they are two independent companies. HP Inc. retained the printing and PC business segments, while HPE retained the technology solutions segments.}

#94-96 1,4 shots gold data falsch mit Joe Kaeser als richtig erkannt. (CEO of Siemens AG from 2013 to 2021)aktuel Ceo Roland Busch (1-3, 5-10)
#125-128= falsche gold label ( Dennis Muilenburg was CEO from 2015 to 2019,) auch falsch: Dave Calhoun chief executive of Boeing from January 2020 to August 7, 2024. (1-10 shots) !!!! seit 2024 ist Kelly Ortberg ceo

#altes wissen: #251-253= Joaquín Duato is the new CEO of Johnson & Johnson (altes wissen:Alex Goros)
# 531-532 Robert Kyncl richtig (altes wissen stefan cooper nur mit 4 shots)
#1176-1179 (akturll bill ready) altes wissen Ben Silbermann

#altes wissen: # barcelona ceo 50-53
#1- ferran reverter
#1-Joan Laporta = seit März 2021 erneut Präsident des FC Barcelona.
#https://www.sport.es/en/news/barca/ferran-reverter-leaves-role-fc-13207809

#1121-1123 John S. Chen annotiert model kennt John Chen alle shots

#300-301 doug parker old (new Robert Isom)

# beide schreibweise im web auffinbar:  oleg belezyrov/ belezerov: 401-406 gold token


In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/company_ceo")

####company hq

In [ ]:
 normalize("company_hq"): [
        ("Apple", "Cupertino"),
        ("Microsoft", "Redmond"),
        ("Tesla", "Austin"),
        ("Amazon", "Seattle"),
        ("Spotify", "Stockholm"),
        ("Rolls-Royce", "London"),
        ("Heineken", "Amsterdam"),
        ("SAP", "Walldorf"),
        ('KONE', 'Espoo'),
       ("Ferrari", "Maranello")
    ],
    #mehr optionen online zu finden 18,24,26
    #falsche data 22
    # 83 ab 5 shots falsch
    # 159 tokenisierung? 10 shots Aber statt Aberdeen
    # 291 übwerall richtig London und 10 shot Amsterdam
    # 401 10 shots falsch wieder, statt frakfurt , essen
    # 437 mit 10 shot Barcelona statt Instambul
    # 524 chicago richtig mit few shots Berlin
    # 636 Bengalore (tokenisierung) Bengal(fehlt der rest für transparenc)

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/company_hq")

###Historische/Zeit- & sonstige Fakten

####president birth year

In [ ]:
("presidents_birth_year"): [
        ("Dwight D. Eisenhower", "1890"), ("Theodore Roosevelt", "1858"), ("Woodrow Wilson", "1856"),
        ("William McKinley", "1843"), ("Herbert Hoover", "1874"), ("Grover Cleveland", "1837"),
        ("Ulysses S. Grant", "1822"), ("Abraham Lincoln", "1809"), ("Chester A. Arthur", "1829"),
        ("Benjamin Harrison", "1833")

        # zero shot 35 fehler subtoken. 12 fehler mit zero shot von 19 samples
        -# 0, 6, typische Fehler (John Adams was born in: antwort: Braintree (now Quincy), Massachusetts
        # 19-20 falsche zahlen



In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/presidents_birth_year")

#### president election year

In [ ]:
normalize("presidents_election_year"): [
        ("Dwight D. Eisenhower", "1952"), ("Theodore Roosevelt", "1904"), ("Woodrow Wilson", "1912"),
        ("William McKinley", "1896"), ("Herbert Hoover", "1928"), ("Grover Cleveland", "1885"),
        ("Ulysses S. Grant", "1869"), ("Abraham Lincoln", "1860"), ("Donald Trump", "2016"),
        ("Benjamin Harrison", "1888")

        # von 19 samples mit 0 shot 2 falsch
        # mit einem shot 0 fehler
        # 2-5 shot einen samples falsch
        # 7 shots 2 samples falsch
        #und 10 shot keinen fehler


In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/presidents_election_year")

####star constellation

In [ ]:
("star constellation"): [
    ("Canopus", "Carina"),
    ("Achernar", "constellation Eridanus"),
    ("Mimosa", "Crux"),
    ("Alnitak", "Orion"),
    ("Rasalhague", "Ophiuchus"),
    ("Algorab", "Corvus"),
    ("Markab", "Pegasus"),
    ("Alpheratz", "Andromeda"),
    ("Kochab", "Ursa Minor"),
    ("Nunki", "Sagittarius")
  ],
  #362 samples, 701 tokens
  # 3 zero shot:  the same  statt Lyra
  # shot 1 macht mehrmals statt richtige antwor carina. beispiel von ersten shot (42-59)
  # 65-66: 3 shot crux beispiel-.  3-10 shots, 121, 127,
  # 163 und 164 (1 shot carina) (2 shot constellation), (3 -10 shot crux) bias problem

  # ab 2 shot gibt nicht nur namen sondern auch constellation (so wie 2 shot beispiel, zb ID 38-39, 42-43, 44-45) teilweise falsch, und teilweise rcihtig obwohl als falsch zählt.
  # ab 3 shots verringert sich das problem (38-41 bleibt bestehen)
  #108, 120, 121, 127, 131 = gleiche phänomen mit constellation und id 120 taucht bis 10 shot auf.


In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/star_constellation")

####pokeman evaluation

In [ ]:
("pokemon evolutions"): [
        ("Eevee", "Vaporeon"), ("Eevee", "Jolteon"), ("Eevee", "Flareon"),
        ("Tyrogue", "Hitmonlee"), ("Tyrogue", "Hitmonchan"),
        ("Tyrogue", "Hitmontop"), ("Pichu", "Pikachu"),
        ("Magikarp", "Gyarados"), ("Remoraid", "Octillery"),
        ("Togepi", "Togetic")
    ],
    # 44 samples 111 subtokens
    # ab 4 shot keine fehler
    #1 shot macht 2 samples faslch und 2 und 3 shots jeweils einen fehler.

    # Mit zero shot falsche token prediction
    # Beispiel: falsche pokeman namen: Statt „Ivysaur“ („Bulbasaur evolves into...“) generiert das Modell „Venusaur“.
# irrelevante begriffe: 23,24: human duck, astro:14

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/pokemon_evolutions")

####superhero archnemesis

In [ ]:
("superhero_archnemesis"): [
        ("Nova", "Annihilus"),
         ("Sentry", "The Void"),
         ("Batwoman", "Alice"),
         ("Shang-Chi", "Wenwu"),
        ("Forge", "Adversary "),
         ("Orion", "Darkseid"),
        ("Mister Miracle", "Granny Goodness"),
         ("Eternals ","Kro"),
       ("Ms. Marvel", "Najma"),
        ("Moon Knight","Arthur Harrow")

        #96 samples
        token 249
        #131-132 wurde "the" klein statt "The" oder nur Joker generiert.

        #few shots Verbesserung:

        """
Fälle mit klarer Verbesserung durch Few-Shot:
Batman → Joker: #4

Captain America → Red Skull: #15–16

Luke Cage → Diamondback: #74–75

Punisher → Jigsaw: #72–73

Black Panther → Killmonger: #20–22

Teenage Mutant Ninja Turtles → Shredder: #178–180
"""

# beispiele mit flaschen aber plausible Token-Vorhersagen:
#Spider-Man	Green Goblin	(Venom	falsch (#8–9)
#Doctor Strange	Baron Mordo	(Dormammu falsch	(#23–25)
#Aquaman	Black Manta	(Ocean Master	falsch (#26–28)
#Black Widow	Taskmaster	(Red Room falsch 	(#68–69)
#Green Lantern	Sinestro	(Parallax	falsch (#13–14)
#Hercules	Hades	(Titan falsch)	(#221–222)
#Superman	Lex Luthor	(Darkseid	falsch (#0–2, ab 2 Shots)

  # Das Modell generiert häufig plausible, aber inkorrekte Antagonisten, was auf Schwierigkeiten
  # bei der präzisen Auswahl zwischen mehreren bekannten Erzfeinden hinweist.
  # Diese Fehler treten sowohl im Zero-Shot-Ansatz als auch verstärkt bei höherer Shot-Anzahl auf,
  # was zeigt, dass die Erhöhung der Shots nicht automatisch zu stabileren oder präziseren Vorhersagen führt.


  # 2-Probleme bei 2-Shot: Bereits korrekte Vorhersagen aus dem 0–1 Shot-Ansatz werden durch Hinzufügen
    # weiterer Beispiele in einigen Fällen verschlechtert, da das Modell durch häufige,
    # aber falsche Alternativen beeinflusst wird.


In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/factual/it/result_10_accuracy/logits/permutation_0/superhero_archnemesis")

#linguistic

#### Adj antonym

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/linguistic/it/result_new/logits/permutation_0/adjective_antonym")
#49-51


####adjective_comparative

In [5]:
rows = [0,1,2,3,4,5,6]

export_compact_table("/content/drive/MyDrive/master_thesis/dataset_multilingual/linguistic"
                    "/it/result_10_accuracy/logits/permutation_0/adjective_comparative",

    rows_to_show = rows,
    out_name     = "adjective_comparative_it",
    only_errors  = False,
    show_title   = False
)

✔︎ PDF : /content/drive/MyDrive/master_thesis/ploted_data_it/adjective_comparative_it.pdf
✔︎ PNG : /content/drive/MyDrive/master_thesis/ploted_data_it/adjective_comparative_it.png


In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/linguistic/it/result_new/logits/permutation_0/adjective_comparative")
#it

####adjective_superlative

Im Few-Shot-Ansatz ist für das Italienische nur eine moderate Verbesserung erkennbar. Die Fehlerzahl bleibt über mehrere Shots hinweg weitgehend stabil, wobei beim 10-Shot-Ansatz sogar eine leichte Verschlechterung der Ergebnisse festzustellen ist. Insgesamt fällt die Lernkurve flach aus, und das Modell zeigt im Vergleich zu anderen Sprachen eine begrenzte Few-Shot-Performance.

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/linguistic/it/result_new/logits/permutation_0/adjective_superlative")




####verb_past_tense

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/linguistic/it/result_new/logits/permutation_0/verb_past_tense")


####word_first_letter

In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/linguistic/it/result_new/logits/permutation_0/word_first_letter")

####word_last_letter

In [6]:
rows = [0,1,2,3,4,5,6]

export_compact_table("/content/drive/MyDrive/master_thesis/dataset_multilingual/linguistic"
                    "/it/result_10_accuracy/logits/permutation_0/word_last_letter",

    rows_to_show = rows,
    out_name     = "word_last_letter_it",
    only_errors  = False,
    show_title   = False
)

✔︎ PDF : /content/drive/MyDrive/master_thesis/ploted_data_it/word_last_letter_it.pdf
✔︎ PNG : /content/drive/MyDrive/master_thesis/ploted_data_it/word_last_letter_it.png


In [ ]:
erroranalyse_relation_new("/content/drive/MyDrive/master_thesis/dataset_multilingual/linguistic/it/result_new/logits/permutation_0/word_last_letter")
